# VacationPy
---

## Starter Code to Import Libraries and Load the Weather and Coordinates Data

In [1]:
# Dependencies and Setup
import hvplot.pandas
import pandas as pd
import requests

# Import API key
from api_keys import geoapify_key


In [2]:
# Load the CSV file created in Part 1 into a Pandas DataFrame
city_data_df = pd.read_csv("output_data/cities.csv")

# Display sample data
city_data_df.head()

City_ID       City      Lat       Lng  Max Temp  Humidity  Cloudiness  \
0        0        sur  22.5667   59.5289     26.25        60         100   
1        1    selfoss  63.9331  -20.9971     -0.53        40           0   
2        2    ushuaia -54.8000  -68.3000      4.81        87          75   
3        3   waitangi -43.9535 -176.5597     13.79        97          98   
4        4  grytviken -54.2811  -36.5092      0.09        63           5   

   Wind Speed Country        Date  
0        1.01      OM  1711898857  
1       12.48      IS  1711898857  
2       11.32      AR  1711898652  
3        1.79      NZ  1711898858  
4        2.91      GS  1711898786

---

### Step 1: Create a map that displays a point for every city in the `city_data_df` DataFrame. The size of the point should be the humidity in each city.

In [3]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.points(x='Lng', y='Lat', 
                                      geo=True, 
                                      hover_cols=['City', 'Humidity'], 
                                      tiles='OSM',
                                      size='Humidity',
                                      color='Humidity',
                                      legend='right',
                                      alpha=.5,
                                      label='City',
                                      coastline=True,
                                      colorbar=False,
                                      )

# Display the map plot
map_plot

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .Points.City :Points   [Lng,Lat]   (Humidity,City)
   .Coastline.I :Feature   [Longitude,Latitude]

In [4]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', cmap='rainbow', by='City',
                                       geo=True, hover_cols=['City', 'Humidity'],
                                       legend='right', tiles='CartoLight', xlim=(-180, 180), ylim=(-90, 90))

# Display the map plot
map_plot

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .NdOverlay.I :NdOverlay   [City]
      :Scatter   [Lng]   (Lat,Humidity,City)

In [5]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', cmap='rainbow', by='City',
                                       geo=True,hover_cols=['City', 'Humidity'],
                                       legend='right', fill_alpha=.5)

# Display the map plot
map_plot

:NdOverlay   [City]
   :Scatter   [Lng]   (Lat,Humidity,City)

### Step 2: Narrow down the `city_data_df` DataFrame to find your ideal weather condition

In [6]:
# Narrow down cities that fit criteria and drop any results with null values
temp_filt = (city_data_df['Max Temp']>15) & (city_data_df['Max Temp']<30)
lat_filt = (city_data_df['Lat']>15) & (city_data_df['Lat']<50)
long_filt = (city_data_df['Lng']>-120) & (city_data_df['Lng']<-80)
hum_filt =(city_data_df['Humidity']>10) & (city_data_df['Humidity']<=100)
ideal_weather_df = city_data_df[temp_filt&lat_filt&hum_filt&long_filt]

# Drop any rows with null values
ideal_weather_df.dropna()

# Display sample data
ideal_weather_df


City_ID                    City      Lat       Lng  Max Temp  Humidity  \
36        36  ciudad lazaro cardenas  17.9583 -102.2000     26.84        50   
100      100            san patricio  28.0170  -97.5169     26.04        74   
107      107          cabo san lucas  22.8909 -109.9124     21.95        67   
130      130         carrizo springs  28.5219  -99.8606     24.34        73   
154      154                 la cruz  23.9167 -106.9000     21.12        77   
183      183          guerrero negro  27.9769 -114.0611     16.39        78   
184      184              la entrada  15.0500  -88.7333     25.55        66   
261      261                picayune  30.5255  -89.6795     23.82        63   
274      274               mcalester  34.9334  -95.7697     20.05        77   
275      275                   crane  31.3974 -102.3501     21.25        56   
326      326                  panaba  21.2833  -88.2667     29.22        48   
332      332   coahuayana de hidalgo  18.7000 -103.6583     28.00        36   
352      352               chihuahua  28.5000 -106.0000     16.78        19   
372      372      brisas de zicatela  15.8369  -97.0419     29.00        52   
424      424                  ixtapa  20.7000 -105.2000     23.46        94   
482      482                  copala  16.6500  -98.9833     28.59        52   
500      500                   prien  30.1819  -93.2738     23.99        88   
557      557         lazaro cardenas  17.9583 -102.2000     26.84        50   

     Cloudiness  Wind Speed Country        Date  
36           26        0.21      MX  1711898798  
100          76        6.57      US  1711898795  
107          20        1.54      MX  1711898720  
130         100        2.57      US  1711898879  
154         100        1.30      MX  1711898883  
183         100        3.87      MX  1711898620  
184          88        0.58      HN  1711898888  
261          96        2.60      US  1711898902  
274         100        5.14      US  1711898784  
275         100        6.19      US  1711898795  
326           0        5.35      MX  1711898915  
332          84        0.77      MX  1711898916  
352         100        7.17      MX  1711898543  
372          37        1.48      MX  1711898923  
424          20        2.06      MX  1711898932  
482          27        1.01      MX  1711898945  
500         100        7.20      US  1711898948  
557          26        0.21      MX  1711898814

### Step 3: Create a new DataFrame called `hotel_df`.

In [7]:
# Use the Pandas copy function to create DataFrame called hotel_df to store the city, country, coordinates, and humidity
columns_to_copy = ['City', 'Country', 'Lat', 'Lng', 'Humidity']
hotel_df = ideal_weather_df[columns_to_copy].copy()

# Add an empty column, "Hotel Name," to the DataFrame so you can store the hotel found using the Geoapify API
hotel_df['Hotel Name'] = ''

# Display sample data
hotel_df

City Country      Lat       Lng  Humidity Hotel Name
36   ciudad lazaro cardenas      MX  17.9583 -102.2000        50           
100            san patricio      US  28.0170  -97.5169        74           
107          cabo san lucas      MX  22.8909 -109.9124        67           
130         carrizo springs      US  28.5219  -99.8606        73           
154                 la cruz      MX  23.9167 -106.9000        77           
183          guerrero negro      MX  27.9769 -114.0611        78           
184              la entrada      HN  15.0500  -88.7333        66           
261                picayune      US  30.5255  -89.6795        63           
274               mcalester      US  34.9334  -95.7697        77           
275                   crane      US  31.3974 -102.3501        56           
326                  panaba      MX  21.2833  -88.2667        48           
332   coahuayana de hidalgo      MX  18.7000 -103.6583        36           
352               chihuahua      MX  28.5000 -106.0000        19           
372      brisas de zicatela      MX  15.8369  -97.0419        52           
424                  ixtapa      MX  20.7000 -105.2000        94           
482                  copala      MX  16.6500  -98.9833        52           
500                   prien      US  30.1819  -93.2738        88           
557         lazaro cardenas      MX  17.9583 -102.2000        50

### Step 4: For each city, use the Geoapify API to find the first hotel located within 10,000 metres of your coordinates.

In [8]:
# Set parameters to search for a hotel
radius = 10000
limit = 20
params = {
    "categories":"accommodation.hotel",
    "apiKey": geoapify_key,
    "limit":limit,
}

# Print a message to follow up the hotel search
print("Starting hotel search")

# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    # get latitude, longitude from the DataFrame
    lat = row.iloc[2]
    long = row.iloc[3]
    
    # Add filter and bias parameters with the current city's latitude and longitude to the params dictionary
    params["filter"] = f"circle:{long},{lat},{radius}"
    params["bias"] = f"proximity:{long},{lat}"
    
    # Set base URL
    base_url = "https://api.geoapify.com/v2/places"


    # Make and API request using the params dictionaty
    name_address = requests.get(base_url, params=params)
    
    # Convert the API response to JSON format
    name_address = name_address.json()
    
    # Grab the first hotel from the results and store the name in the hotel_df DataFrame
    try:
        hotel_df.loc[index, "Hotel Name"] = name_address["features"][0]["properties"]["name"]
    except (KeyError, IndexError):
        # If no hotel is found, set the hotel name as "No hotel found".
        hotel_df.loc[index, "Hotel Name"] = "No hotel found"
        
    # Log the search results
    print(f"{hotel_df.loc[index, 'City']} - nearest hotel: {hotel_df.loc[index, 'Hotel Name']}")

# Display sample data
hotel_df

Starting hotel search
ciudad lazaro cardenas - nearest hotel: No hotel found
san patricio - nearest hotel: No hotel found
cabo san lucas - nearest hotel: No hotel found
carrizo springs - nearest hotel: No hotel found
la cruz - nearest hotel: No hotel found
guerrero negro - nearest hotel: No hotel found
la entrada - nearest hotel: No hotel found
picayune - nearest hotel: No hotel found
mcalester - nearest hotel: No hotel found
crane - nearest hotel: No hotel found
panaba - nearest hotel: No hotel found
coahuayana de hidalgo - nearest hotel: No hotel found
chihuahua - nearest hotel: No hotel found
brisas de zicatela - nearest hotel: No hotel found
ixtapa - nearest hotel: No hotel found
copala - nearest hotel: No hotel found
prien - nearest hotel: No hotel found
lazaro cardenas - nearest hotel: No hotel found


City Country      Lat       Lng  Humidity  \
36   ciudad lazaro cardenas      MX  17.9583 -102.2000        50   
100            san patricio      US  28.0170  -97.5169        74   
107          cabo san lucas      MX  22.8909 -109.9124        67   
130         carrizo springs      US  28.5219  -99.8606        73   
154                 la cruz      MX  23.9167 -106.9000        77   
183          guerrero negro      MX  27.9769 -114.0611        78   
184              la entrada      HN  15.0500  -88.7333        66   
261                picayune      US  30.5255  -89.6795        63   
274               mcalester      US  34.9334  -95.7697        77   
275                   crane      US  31.3974 -102.3501        56   
326                  panaba      MX  21.2833  -88.2667        48   
332   coahuayana de hidalgo      MX  18.7000 -103.6583        36   
352               chihuahua      MX  28.5000 -106.0000        19   
372      brisas de zicatela      MX  15.8369  -97.0419        52   
424                  ixtapa      MX  20.7000 -105.2000        94   
482                  copala      MX  16.6500  -98.9833        52   
500                   prien      US  30.1819  -93.2738        88   
557         lazaro cardenas      MX  17.9583 -102.2000        50   

         Hotel Name  
36   No hotel found  
100  No hotel found  
107  No hotel found  
130  No hotel found  
154  No hotel found  
183  No hotel found  
184  No hotel found  
261  No hotel found  
274  No hotel found  
275  No hotel found  
326  No hotel found  
332  No hotel found  
352  No hotel found  
372  No hotel found  
424  No hotel found  
482  No hotel found  
500  No hotel found  
557  No hotel found

### Step 5: Add the hotel name and the country as additional information in the hover message for each city in the map.

In [9]:
%%capture --no-display
# Create a map plot with points for each city, where size represents humidity
map_plot = hotel_df.hvplot.points(x='Lng', y='Lat', 
                                      geo=True, 
                                      hover_cols=['City', 'Humidity','Hotel Name', 'Country'], 
                                      tiles='OSM',
                                      size='Humidity',
                                      color='Lat',
                                      legend='right',
                                      alpha=.5,
                                      coastline=True,
                                      colorbar=False,
                                      xlim=(-180, 180), ylim=(-60, 70))

# Display the map plot
map_plot

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .Points.I    :Points   [Lng,Lat]   (Humidity,City,Hotel Name,Country)
   .Coastline.I :Feature   [Longitude,Latitude]

In [10]:
%%capture --no-display

# Configure the map plot
map_plot = hotel_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', cmap='rainbow', by='City',
                                       geo=True,hover_cols=['City', 'Humidity', 'Hotel Name','Country'],
                                       legend='right', fill_alpha=.5)

# Display the map plot
map_plot

:NdOverlay   [City]
   :Scatter   [Lng]   (Lat,Humidity,City,Hotel Name,Country)